In [1]:

import transformers
import json
import sys
import os
import datasets
squad_dataset = datasets.load_dataset('squad')
from datasets import concatenate_datasets, load_dataset

covid_file = '../data/COVID-QA.json'
bio_file = '../bioASQ/bioASQ.json'

def make_and_save_full_dataset(train, valid, test, path):
    full_data = datasets.dataset_dict.DatasetDict({'train':train, 'validation':valid, 'test': test})
    full_data.save_to_disk(path)

def get_dataset(filename):
    return datasets.load_dataset('custom_squad.py', data_files= {'train':filename})['train']

Reusing dataset squad (C:\Users\unitu\.cache\huggingface\datasets\squad\plain_text\1.0.0\6b6c4172d0119c74515f44ea0b8262efe4897f2ddb6613e5e915840fdc309c16)


In [2]:
import run_qa

def run_gradual_ft(output_dir, checkpoint, covid_val):
    !python run_qa.py \
      --model_name_or_path {checkpoint} \
      --dataset_name ../data/full_squad_covidQA/ \
      --do_train \
      --do_eval \
      --do_predict \
      --per_device_train_batch_size 40\
      --per_device_eval_batch_size 40\
      --evaluation_strategy "no" \
      --save_strategy "no" \
      --logging_strategy "epoch" \
      --learning_rate 2e-5 \
      --num_train_epochs 1 \
      --max_seq_length 384 \
      --doc_stride 128 \
      --output_dir {output_dir} \
      --overwrite_output_dir

In [3]:
data_files = {}
data_files["train"] = covid_file

covid_qa = get_dataset(covid_file)
bio_qa = get_dataset(bio_file)

squad_qa = concatenate_datasets([squad_dataset['train'], squad_dataset['validation']])
covid_and_squad_dataset_path = "../data/full_squad_covidQA"

Using custom data configuration default-a396986d6b3a2375
Reusing dataset squad (C:\Users\unitu\.cache\huggingface\datasets\squad\default-a396986d6b3a2375\0.0.0\cb00e306c4924563ce3d1292a1ce1b86b2753dab6285ce43c87b39c5bda3ef4e)
Using custom data configuration default-8fdbe041288a2f4d
Reusing dataset squad (C:\Users\unitu\.cache\huggingface\datasets\squad\default-8fdbe041288a2f4d\0.0.0\cb00e306c4924563ce3d1292a1ce1b86b2753dab6285ce43c87b39c5bda3ef4e)


In [4]:
k_fold = 5
K = 6
for i in range(k_fold):
    covid_fold = covid_qa.shard(k_fold, i)

    covid_test = covid_fold.shard(2, 0)
    covid_val = covid_fold.shard(2, 1)
    covid_train = concatenate_datasets([covid_qa.shard(k_fold, j) for j in range(k_fold) if j != i])

    #make_and_save_full_dataset(covid_train, squad_qa, covid_val, covid_test, covid_and_squad_dataset_path)

    checkpoint = 'roberta-base'
    cur_dir = '../models/gradual_ft_w_bioASQ_lr2e-5/split_' + str(i)

    #log_file = open(cur_dir + "/log_file.txt","w+")
    #sys.stdout = log_file

    squad_qa.shuffle()
    bio_qa.shuffle()

    num_of_shards = int(K/2)
    squad_qa_shards = [squad_qa.shard(num_of_shards,i) for i in range(num_of_shards)]
    bio_qa_shards = [bio_qa.shard(num_of_shards,i) for i in range(num_of_shards)]
    print(f'Gradual finetuning with K={K} ({K//2} per SQuAD and bioASQ)')
    for n in range(K+1):
        output_dir = cur_dir + '/checkpoint_' + str(n)
        if n < K//2:
            squad_qa_cur = concatenate_datasets(squad_qa_shards)
            full_dataset = concatenate_datasets([squad_qa_cur, covid_train])
            _ = squad_qa_shards.pop()
        elif n < K:
            bio_qa_cur = concatenate_datasets(bio_qa_shards)
            full_dataset = concatenate_datasets([bio_qa_cur, covid_train])
            _ = bio_qa_shards.pop()
        else:
            full_dataset = covid_train

        make_and_save_full_dataset(full_dataset, covid_val, covid_test, covid_and_squad_dataset_path)

        run_gradual_ft(output_dir, checkpoint, covid_val)

        checkpoint = output_dir

    #log_file.close()
#sys.stdout = sys.__stdout__

Loading cached shuffled indices for dataset at C:\Users\unitu\.cache\huggingface\datasets\squad\plain_text\1.0.0\6b6c4172d0119c74515f44ea0b8262efe4897f2ddb6613e5e915840fdc309c16\cache-30b2dcc23b00412a.arrow


Gradual finetuning with K=6 (3 per SQuAD and bioASQ)


[INFO|configuration_utils.py:530] 2021-07-09 00:01:43,549 >> loading configuration file https://huggingface.co/roberta-base/resolve/main/config.json from cache at C:\Users\unitu/.cache\huggingface\transformers\733bade19e5f0ce98e6531021dd5180994bb2f7b8bd7e80c7968805834ba351e.35205c6cfc956461d8515139f0f8dd5d207a2f336c0c3a83b4bc8dca3518e37b
[INFO|configuration_utils.py:566] 2021-07-09 00:01:43,550 >> Model config RobertaConfig {
  "architectures": [
    "RobertaForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "eos_token_id": 2,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-05,
  "max_position_embeddings": 514,
  "model_type": "roberta",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "transformers_version": "4.8.1",
  "type_vocab_size": 1,
  "u

07/09/2021 00:01:42 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1distributed training: False, 16-bits training: False
07/09/2021 00:01:42 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(
_n_gpu=1,
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_pin_memory=True,
ddp_find_unused_parameters=None,
debug=[],
deepspeed=None,
disable_tqdm=False,
do_eval=True,
do_predict=True,
do_train=True,
eval_accumulation_steps=None,
eval_steps=500,
evaluation_strategy=IntervalStrategy.NO,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
gradient_accumulation_steps=1,
greater_is_better=None,
group_by_length=False,
ignore_data_skip=False,
label_names=None,
label_smoothing_factor=0.0,
learning_rate=2e-05,
length_column_name=length,
load_best_model_at_end=False,
local_rank=-1,
log_level=-1,
log_level_replica=-1,
log_on_each_node=True,
logging_dir=../models


100%|##########| 3730/3730 [42:06<00:00,  2.27it/s]
                                                   

100%|##########| 3730/3730 [42:06<00:00,  2.27it/s][INFO|trainer.py:1349] 2021-07-09 00:44:04,835 >> 

Training completed. Do not forget to share your model on huggingface.co/models =)



                                                   

100%|##########| 3730/3730 [42:06<00:00,  1.48it/s]
[INFO|trainer.py:1900] 2021-07-09 00:44:04,837 >> Saving model checkpoint to ../models/gradual_ft_w_bioASQ_lr2e-5/split_0/checkpoint_0
[INFO|configuration_utils.py:364] 2021-07-09 00:44:04,837 >> Configuration saved in ../models/gradual_ft_w_bioASQ_lr2e-5/split_0/checkpoint_0\config.json
[INFO|modeling_utils.py:898] 2021-07-09 00:44:05,483 >> Model weights saved in ../models/gradual_ft_w_bioASQ_lr2e-5/split_0/checkpoint_0\pytorch_model.bin
[INFO|tokenization_utils_base.py:1948] 2021-07-09 00:44:05,484 >> tokenizer config file saved in ../models/gradual_ft_w_bioASQ_lr2e-5/split_0/checkpoint_0\to

...

 99%|#########9| 155/156 [00:25<00:00,  6.05it/s]

  0%|          | 0/201 [00:00<?, ?it/s]

  1%|          | 2/201 [00:00<00:20,  9.66it/s]

  3%|2         | 6/201 [00:00<00:15, 12.21it/s]

  4%|3         | 8/201 [00:00<00:15, 12.30it/s]

  5%|4         | 10/201 [00:00<00:14, 13.62it/s]

  6%|5         | 12/201 [00:00<00:13, 14.44it/s]

  7%|6         | 14/201 [00:00<00:12, 15.04it/s]

  8%|8         | 17/201 [00:01<00:11, 15.59it/s]

 10%|#         | 21/201 [00:01<00:09, 18.13it/s]

 11%|#1        | 23/201 [00:01<00:10, 17.16it/s]

 12%|#2        | 25/201 [00:01<00:11, 15.12it/s]

 14%|#3        | 28/201 [00:01<00:10, 16.70it/s]

 15%|#5        | 31/201 [00:01<00:09, 17.14it/s]

 16%|#6        | 33/201 [00:01<00:10, 16.21it/s]

 17%|#7        | 35/201 [00:02<00:10, 16.15it/s]

 18%|#8        | 37/201 [00:02<00:10, 16.30it/s]

 19%|#9        | 39/201 [00:02<00:09, 16.21it/s]

 20%|##        | 41/201 [00:02<00:10, 15.62it/s]

 21%|##1       | 43/201 [00:02<00:10, 15.37it/s]

 22%|##2   

07/09/2021 12:15:10 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1distributed training: False, 16-bits training: False
07/09/2021 12:15:10 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(
_n_gpu=1,


[INFO|configuration_utils.py:528] 2021-07-09 12:15:11,486 >> loading configuration file ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_5\config.json
[INFO|configuration_utils.py:566] 2021-07-09 12:15:11,487 >> Model config RobertaConfig {
  "_name_or_path": "../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_4",
  "architectures": [
    "RobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "eos_token_id": 2,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,

adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_pin_memory=True,
ddp_find_unused_parameters=None,
debug=[],
deepspeed=None,
disable_tqdm=False,
do_eval=True,
do_predict=True,
do_train=True,
eval_accumulation_steps=None,
eval_steps=500,
evaluation_strategy=IntervalStrategy.NO,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
gradient_accumulation_steps=1,
greater_is_better=None,
group_by_length=False,
ignore_data_skip=False,
label_names=None,
label_smoothing_factor=0.0,
learning_rate=2e-05,
length_column_name=length,
load_best_model_at_end=False,
local_rank=-1,
log_level=-1,
log_level_replica=-1,
log_on_each_node=True,
logging_dir=../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_6\runs\Jul09_12-15-10_DESKTOP-1CU6Q06,
logging_first_step=False,
logging_steps=500,
logging_strategy=IntervalStrategy.EPOCH,
lr_scheduler_type=SchedulerType.LINEAR,
max_grad_norm=1.0,
max_steps=-


  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-05,
  "max_position_embeddings": 514,
  "model_type": "roberta",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "transformers_version": "4.8.1",
  "type_vocab_size": 1,
  "use_cache": true,
  "vocab_size": 50265
}

[INFO|tokenization_utils_base.py:1651] 2021-07-09 12:15:11,500 >> Didn't find file ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_5\added_tokens.json. We won't load it.
[INFO|tokenization_utils_base.py:1715] 2021-07-09 12:15:11,500 >> loading file ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_5\vocab.json
[INFO|tokenization_utils_base.py:1715] 2021-07-09 12:15:11,500 >> loading file ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_5\merges.txt
[INFO|tokenization_utils_base.py:1715] 2021-07-09 12:15:11,500 >> loading file ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_5\tokenizer.json
[INF

07/09/2021 12:27:18 - INFO - utils_qa -   Post-processing 202 example predictions split into 6246 features.
07/09/2021 12:27:35 - INFO - utils_qa -   Saving predictions to ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_6\predict_predictions.json.
07/09/2021 12:27:35 - INFO - utils_qa -   Saving nbest_preds to ../models/gradual_ft_w_bioASQ_lr2e-5/split_4/checkpoint_6\predict_nbest_predictions.json.
***** predict metrics *****
  predict_samples  =    6246
  test_exact_match = 42.5743
  test_f1          = 68.1846


 75%|#######5  | 937/1244 [07:37<02:29,  2.05it/s]